# TCP Plot Tool
Copyright © 2020 Renan Cammarosano and Alejandro ?

_Licensed under GNU GPLv3_

#### Libraries import
We start by importing required python libraries, used for advanced math calculations and data visualization

In [1]:
import numpy
import plotly.graph_objects as go
from plotly.offline import init_notebook_mode, iplot

numpy.seterr(all="ignore")
init_notebook_mode()

#### Main variables
Then we define the main values that are going to be used as constants and values that going to be iterated

In [2]:
steps = 500

In [3]:
sessions = 5
cell_number = 1000000
lethal_single_dose = 30
dose_per_session = 12

In [4]:
coupling_min = 4.5
coupling_max = 5.5

In [5]:
gamma_min = 6.5
gamma_max = 7.5

In [6]:
tcp_min = 0.0
tcp_max = 1.0

#### Loop only variables
Then we declare the variables that are going to be used only to store temporary information to support the loop program

In [7]:
float_rounding = 4

In [8]:
coupling_increment = (coupling_max-coupling_min)/steps
gamma_increment = (gamma_max-gamma_min)/steps

In [9]:
coupling = coupling_min
gamma = gamma_min

In [10]:
result_coupling = []
result_gamma = []
result_tumor_control_probability = []

#### Main loop

In [11]:
### Main loop

# store initial coupling to reset between each y loop
coupling_start = coupling

y_steps_count = 0
# GAMMA LOOP
while y_steps_count<steps:

    coupling = coupling_start
    x_steps_count = 0
    # COUPLING LOOP
    while x_steps_count<steps:
        # get normalized dose
        normalized_dose = dose_per_session/lethal_single_dose

        # preinitialize list of accumulated doses
        acc_doses = [None]*(sessions+1)

        # set first session dose (skip zero to match session number with list index)
        session_count = 1
        acc_doses[session_count] = normalized_dose

        # SESSION LOOP: iterate each session by acumulating the dose from previous session
        while session_count<sessions:
            session_count += 1
            prev_dose = acc_doses[session_count-1]
            try:
                acc_doses[session_count] = prev_dose+normalized_dose*((1-prev_dose)/(1-coupling*prev_dose))
            except ZeroDivisionError:
                acc_doses[session_count] = None
            except TypeError:
                acc_doses[session_count] = None

        # calculated cell survival from accumulated dose result
        try:
            cell_survival = numpy.power((1-acc_doses[session_count]), gamma)
        except TypeError:
            cell_survival = None

        # calculate tumor control probability with
        try:
            tumor_control_probability = numpy.exp(-(cell_number*cell_survival))
        except TypeError:
            tumor_control_probability = 0
        
        # change to 0 or 1 all result not between 0.0 and 1.0
        if tumor_control_probability < 0.0:
            tumor_control_probability = 0
        elif tumor_control_probability > 1.0:
            tumor_control_probability = 1

        # store values in result lists and filter by tcp range
        if tcp_min < tumor_control_probability < tcp_max:
            result_coupling.append(coupling)
            result_gamma.append(gamma)
            result_tumor_control_probability.append(tumor_control_probability)
        

        # increment coupling and step
        coupling = round(coupling+coupling_increment,float_rounding)
        x_steps_count += 1

    # increment gamma and step
    gamma = round(gamma+gamma_increment,float_rounding)
    y_steps_count += 1

#### Display result

In [12]:
data = go.Scatter3d({
    'x':result_coupling,
    'y':result_gamma,
    'z':result_tumor_control_probability,
    'mode':'markers',
    'marker': {
        'size':1
        }
    }
)

layout = {
    'xaxis_title':'Coupling (x)',
    'yaxis_title':'Gamma (y)',
    'zaxis_title':'TCP (z)',
}


fig = go.Figure(data)
fig.update_layout(scene=layout)


iplot(fig)